In [13]:
# %% General Modules
import numpy as np
import pandas as pd
import os
# %% Special Modules - deep learning
import torch
from torch.utils.data import TensorDataset

# %% Internal Modules
#from utils.file_utils import save_pkl

# %%

# %% [markdown]
## Main

# %% OnI: Instance Level Data
def filter_bag_inst(path, filt):
    #### read csv 
    #path = "inst.csv"
    #print(path)
    data = pd.read_csv(path)
    #print(dataInst.shape)
    
    if filt:
        dict1 = data.groupby('bag')['bag'].agg('count').to_dict()
        l = [k for k, v in dict1.items() if v < 4]
        data1 = data[~data['bag'].isin(l)]
    else:
        data1 = data
        
    return data1

In [14]:
# dict1 = dataInst.groupby('bag')['bag'].agg('count').to_dict()

# [k for k, v in dict1.items() if v < 4]

In [15]:
dataInst = filter_bag_inst("inst.csv", True)

In [16]:
dataInst

inst  bag  case label    feat1    feat2     feat3   feat4  \
0    10_S_3_0.jpeg    1     1   CTR  0.76374  0.29191  0.046722  233040   
1    10_S_3_1.jpeg    1     1   CTR  0.76065  0.31171  0.049396  481020   
2    10_S_3_2.jpeg    1     1   CTR  0.71368  0.37529  0.066800   98261   
3    10_S_3_3.jpeg    1     1   CTR  0.77691  0.28980  0.033200  191120   
4    10_S_3_0.jpeg    1     1   CTR  0.75604  0.29954  0.047077   16827   
..             ...  ...   ...   ...      ...      ...       ...     ...   
931   9_S_4_5.jpeg   56    56  CASE  0.77882  0.31092  0.003233  105140   
932   9_S_4_6.jpeg   56    56  CASE  0.76772  0.34165  0.017370   46658   
933   9_S_4_7.jpeg   56    56  CASE  0.79073  0.25687  0.062174  214650   
934   9_S_4_8.jpeg   56    56  CASE  0.78463  0.27471  0.055576   79537   
935   9_S_4_9.jpeg   56    56  CASE  0.78253  0.27665  0.041314   65996   

       feat5  feat6  ...  feat306  feat307  feat308  feat309  feat310  \
0    3820.30  297.0  ...  100.660  140.340  168.830  190.920  208.680   
1    2109.70  424.5  ...  171.880  246.630  295.980  343.030  384.650   
2    1213.10  230.0  ...   68.448   98.957  116.950  133.020  146.080   
3    1375.00  323.0  ...  115.630  164.630  195.310  228.990  258.490   
4     494.91  130.0  ...   25.719   42.270   50.719   59.979   69.719   
..       ...    ...  ...      ...      ...      ...      ...      ...   
931  1781.90  175.0  ...   90.463  119.400  141.000  156.720  171.220   
932   471.29  110.0  ...  144.450  193.930  209.010  219.010  228.010   
933  1850.40  185.5  ...  191.850  254.030  282.810  304.250  324.250   
934   530.25  167.5  ...  154.300  219.450  250.200  274.010  290.100   
935   409.91  118.0  ...  184.190  229.750  265.090  285.890  303.360   

     feat311  feat312  feat313  feat314  feat315  
0    225.990  241.960  255.340   268.34   288.34  
1    418.630  446.500  466.710   484.43   508.43  
2    157.650  167.400  176.430   187.14   203.61  
3    275.800  291.690  304.990   317.97   338.99  
4     79.049   87.757   96.748   105.21   112.72  
..       ...      ...      ...      ...      ...  
931  183.810  195.480  206.920   219.14   236.93  
932  235.910  243.750  251.010   259.01   266.01  
933  341.830  356.780  370.890   389.27   430.03  
934  302.070  310.790  318.200   326.66   334.20  
935  315.220  326.560  339.560   353.00   367.56  

[928 rows x 319 columns]

In [17]:
# %% Assign into NumPy Array
insts = np.array( dataInst.iloc[:,0] )
bags = np.array( dataInst.iloc[:,1] )
cases = np.array( dataInst.iloc[:,2] )
labels = np.array( dataInst.iloc[:,3] )
feats = np.array( dataInst.iloc[:,4:] )

# %% PyTorch Tensor
label2bool = np.array([True if l == 'CASE' else False for l in labels])
data = TensorDataset(torch.Tensor(feats), torch.Tensor(label2bool))

In [18]:
dataInst.iloc[:,1:4].head()

bag  case label
0    1     1   CTR
1    1     1   CTR
2    1     1   CTR
3    1     1   CTR
4    1     1   CTR

In [19]:
# %% Bag Level Data
dataBag = dataInst.iloc[:,1:4]
print( dataBag.shape )
###
dataBag = dataBag.drop_duplicates()
dataBag = dataBag.rename( columns={
	'bag': 'slide_id',
	'case': 'case_id'
} )
dataBag.to_csv("bag.csv", index = False)

(928, 3)


In [20]:
# %% OnI: Bag Level Data
# path = "{}/bag.csv".format( args.dir_oniput )
# print(path)
# dataBag.to_csv( path, index=False )

# %% List of Bags
bags_unique = np.array(dataBag['slide_id'])
print(bags_unique)

[ 1  2  3  4  5  6  7  8  9 11 12 13 14 15 16 17 18 19 20 21 22 23 24 25
 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 43 44 45 46 47 48 49 50 51
 52 53 54 55 56]


In [21]:
# %% Instances in Every Bag
dir = "{}/bags".format('/Users/chitrakbanerjee/Desktop/omics/new_dev')
print(dir)
os.makedirs( dir, exist_ok=True )
###
insts_in_bags = {}
for b in bags_unique: # this iterates 56 times
    # array of 1:56
    insts_sub = np.where(bags == b)[0]
    # for each of 56 subjects tensor of features
    feats_sub = data.tensors[0][insts_sub,:]
    # insts in bag
    insts_in_bags[b] = insts[insts_sub]
    path = "{}/{}.pt".format( dir, b )
    #print(path)
    torch.save( feats_sub, path )
    #print(insts_sub, feats_sub, insts_in_bags[b])
    #print(insts_sub.shape, feats_sub.shape, insts_in_bags[b].shape)

###### this code is redundant    
# %% Cell Counts
# for ( key, values ) in insts_in_bags.items():
# 	print( str(key) + ':' + str( len(values) ) )

# # %%
# path = "{}/insts_in_bags.pkl".format( args.dir_oniput )
# print(path)
# save_pkl( path, insts_in_bags )

# # %%

# # %% [markdown]
# ## EoF

/Users/chitrakbanerjee/Desktop/omics/new_dev/bags


In [22]:
# %% [markdown]
## Command Line Interfaces

# %% Creating a Parser
# import argparse
# parser = argparse.ArgumentParser()

# # %% Adding Arguments
# dir_project = '/SFS/user/ry/ohjihw/project/015'
# parser.add_argument( '--dir_project', type=str, default=dir_project )
# parser.add_argument( '--dir_code', type=str, default='code/python' )
# parser.add_argument( '--dir_oniput', type=str, default='oniput' )
# parser.add_argument( '--dir_split', type=str, default='split' )
# ###
# parser.add_argument( '--job_data', type=str, default='20230412-1-HM' )
# #parser.add_argument( '--job_task', type=str, default='Glomeruli' )
# parser.add_argument( '--job_task', type=str, default='Tubules' )
# parser.add_argument( '--job_label', type=str, default='CASE' )
# ###
# parser.add_argument( '--seed', type=int, default=1 )
# ###
# #parser.add_argument( '--cv_fold', type=int, default=100 )
# parser.add_argument( '--cv_fold', type=int, default=1 )
# #parser.add_argument( '--cv_val', type=float, default=0.2 )
# parser.add_argument( '--cv_val', type=float, default=0.0 )
# #parser.add_argument( '--cv_test', type=float, default=0.2 )
# parser.add_argument( '--cv_test', type=float, default=0.0 )
# parser.add_argument( '--cv_train', type=float, default=1.0 )
# parser.add_argument( '--cv_equal', type=bool, default=True )

# # %% Parsing Arguments
# in_ipython = hasattr(__builtins__,'__IPYTHON__')
# args = parser.parse_args("") if in_ipython else parser.parse_args()
# for ( key, value ) in vars(args).items():
# 	print( 'args' + '.' + key + ':', value )

# # %%

# # %% [markdown]
# ## Header

# # %% Working Directory
import os
# args.dir_code = os.path.join( args.dir_project, args.dir_code )
# print( 'args.dir_code:', args.dir_code )
# os.chdir( args.dir_code )
# args.dir_oniput = os.path.join( args.dir_project, args.dir_oniput )
# args.dir_oniput = os.path.join( args.dir_oniput, args.job_data )
# args.dir_oniput = os.path.join( args.dir_oniput, args.job_task )
# print( 'args.dir_ioput:', args.dir_oniput )
# args.dir_split = os.path.join( args.dir_oniput, args.dir_split )
# os.makedirs( args.dir_split, exist_ok=True )

# %% General Modules
import numpy as np
import pandas as pd
os.path.join('/Users/chitrakbanerjee/Desktop/omics/new_dev/')
# %% Internal Modules
from datasets.dataset_generic import Generic_WSI_Classification_Dataset
from datasets.dataset_generic import save_splits

# %%

# %% [markdown]
## Preprocessing

# %% Data
# if ( args.job_data == '20210903-1-AT - AD' ):
n_classes = 2
seed =1
cv_fold =5
cv_val =0.2
cv_test=0.2
cv_train =1.0
cv_equal =True

dataset = Generic_WSI_Classification_Dataset(csv_path = "bag.csv",
                        label_dict = { "CTR": 0, "CASE": 1},seed = 1, 
                                             patient_strat=True, ignore=[])
# elif ( args.job_data == '20230412-1-HM' ):
# 	args.n_classes = 2
# 	dataset = Generic_WSI_Classification_Dataset(
# 		csv_path = os.path.join( args.dir_oniput, 'bag.csv' ),
# 		label_dict = { 'CTR': 0, args.job_label: 1 },
# 		seed=args.seed, patient_strat=True, ignore=[]
# 	)
# else:
# 	raise NotImplementedError

# %%

# %% [markdown]
## Main


# %% Preparation
num_slides_cls = np.array([len(cls_ids) for cls_ids in dataset.patient_cls_ids])
val_num = np.round( num_slides_cls * cv_val ).astype(int)
test_num = np.round( num_slides_cls * cv_test ).astype(int)
###
if cv_equal is True:
    val_num = [ min(val_num) for n in val_num ]
    test_num = [ min(test_num) for n in test_num ]
###
dataset.create_splits(
    k = cv_fold,
    val_num = val_num, test_num = test_num,
    label_frac = cv_train)

# %% Run: Split
for f in range(cv_fold):
    dataset.set_splits()
    descriptor_df = dataset.test_split_gen( return_descriptor=True )
    splits = dataset.return_splits( from_id=True )
    filename = '{}_{}_{}_{}'.format(
        int( 100 * cv_val ), int( 100 * cv_test ), cv_fold, f
    )
    save_splits( splits, ['train', 'val', 'test'], os.path.join(
        'split', filename + '.csv') )
    save_splits( splits, ['train', 'val', 'test'], os.path.join(
        'split', filename + '_bool' + '.csv'
    ), boolean_style=True )
    descriptor_df.to_csv( os.path.join(
        'split', filename + '_descriptor' + '.csv'
    ) )

# %%

# %% [markdown]
## EoF


label column: label
label dictionary: {'CTR': 0, 'CASE': 1}
number of classes: 2
slide-level counts:  
 0    37
1    16
Name: label, dtype: int64
Patient-LVL; Number of samples registered in class 0: 37
Slide-LVL; Number of samples registered in class 0: 37
Patient-LVL; Number of samples registered in class 1: 16
Slide-LVL; Number of samples registered in class 1: 16

number of training samples: 41
number of samples in cls 0: 31
number of samples in cls 1: 10

number of val samples: 6
number of samples in cls 0: 3
number of samples in cls 1: 3

number of test samples: 6
number of samples in cls 0: 3
number of samples in cls 1: 3



number of training samples: 41
number of samples in cls 0: 31
number of samples in cls 1: 10

number of val samples: 6
number of samples in cls 0: 3
number of samples in cls 1: 3

number of test samples: 6
number of samples in cls 0: 3
number of samples in cls 1: 3



number of training samples: 41
number of samples in cls 0: 31
number of samples in cls 1: 1

In [7]:
import torch
import torch.nn as nn
import torch.nn.functional as F
from utils.utils import initialize_weights
import numpy as np

"""
Attention Network without Gating (2 fc layers)
args:
	L: input feature dimension
	D: hidden layer dimension
	dropout: whether to use dropout (p = 0.25)
	n_classes: number of classes 
"""
class Attn_Net(nn.Module):
	#Or def __init__(self, L = 1024, D = 256, dropout = False, n_classes = 1):
	#def __init__( self, L=50, D=30, dropout=False, n_classes=1 ): #RL
	def __init__( self, L=207, D=50, dropout=False, n_classes=1 ): #RL
		super(Attn_Net, self).__init__()
		self.module = [
			nn.Linear(L, D),
			nn.Tanh()]

		if dropout:
			self.module.append(nn.Dropout(0.25))

		self.module.append(nn.Linear(D, n_classes))
		
		self.module = nn.Sequential(*self.module)
	
	def forward(self, x):
		return self.module(x), x # N x n_classes

"""
Attention Network with Sigmoid Gating (3 fc layers)
args:
	L: input feature dimension
	D: hidden layer dimension
	dropout: whether to use dropout (p = 0.25)
	n_classes: number of classes 
"""
class Attn_Net_Gated(nn.Module):
	#Or def __init__(self, L = 1024, D = 256, dropout = False, n_classes = 1):
	#def __init__( self, L=50, D=30, dropout=False, n_classes=1 ): #RL
	def __init__( self, L=207, D=50, dropout=False, n_classes=1 ): #RL
		super(Attn_Net_Gated, self).__init__()
		self.attention_a = [
			nn.Linear(L, D),
			nn.Tanh()]
		
		self.attention_b = [nn.Linear(L, D),
							nn.Sigmoid()]
		if dropout:
			self.attention_a.append(nn.Dropout(0.25))
			self.attention_b.append(nn.Dropout(0.25))

		self.attention_a = nn.Sequential(*self.attention_a)
		self.attention_b = nn.Sequential(*self.attention_b)
		
		self.attention_c = nn.Linear(D, n_classes)

	def forward(self, x):
		a = self.attention_a(x)
		b = self.attention_b(x)
		A = a.mul(b)
		A = self.attention_c(A)  # N x n_classes
		return A, x

"""
args:
	gate: whether to use gated attention network
	size_arg: config for network size
	dropout: whether to use dropout
	k_sample: number of positive/neg patches to sample for instance-level training
	dropout: whether to use dropout (p = 0.25)
	n_classes: number of classes 
	instance_loss_fn: loss function to supervise instance-level training
	subtyping: whether it's a subtyping problem
"""
class CLAM_SB(nn.Module):
	def __init__(self, gate = True, size_arg = "small", dropout = False, k_sample=8, n_classes=2,
		instance_loss_fn=nn.CrossEntropyLoss(), subtyping=False):
		super(CLAM_SB, self).__init__()
		#Or self.size_dict = {"small": [1024, 512, 256], "big": [1024, 512, 384]}
		#self.size_dict = { "small": [50, 30, 15], "big": [50, 30, 15] } #RL
		self.size_dict = { "small": [207, 100, 50], "big": [207, 100, 50] } #RL
		size = self.size_dict[size_arg]
		fc = [nn.Linear(size[0], size[1]), nn.ReLU()]
		if dropout:
			fc.append(nn.Dropout(0.25))
		if gate:
			attention_net = Attn_Net_Gated(L = size[1], D = size[2], dropout = dropout, n_classes = 1)
		else:
			attention_net = Attn_Net(L = size[1], D = size[2], dropout = dropout, n_classes = 1)
		fc.append(attention_net)
		self.attention_net = nn.Sequential(*fc)
		self.classifiers = nn.Linear(size[1], n_classes)
		instance_classifiers = [nn.Linear(size[1], 2) for i in range(n_classes)]
		self.instance_classifiers = nn.ModuleList(instance_classifiers)
		self.k_sample = k_sample
		self.instance_loss_fn = instance_loss_fn
		self.n_classes = n_classes
		self.subtyping = subtyping

		initialize_weights(self)

	def relocate(self):
		device=torch.device("cuda" if torch.cuda.is_available() else "cpu")
		self.attention_net = self.attention_net.to(device)
		self.classifiers = self.classifiers.to(device)
		self.instance_classifiers = self.instance_classifiers.to(device)
	
	@staticmethod
	def create_positive_targets(length, device):
		return torch.full((length, ), 1, device=device).long()
	@staticmethod
	def create_negative_targets(length, device):
		return torch.full((length, ), 0, device=device).long()
	
	#instance-level evaluation for in-the-class attention branch
	def inst_eval(self, A, h, classifier): 
		device=h.device
		if len(A.shape) == 1:
			A = A.view(1, -1)
		top_p_ids = torch.topk(A, self.k_sample)[1][-1]
		top_p = torch.index_select(h, dim=0, index=top_p_ids)
		top_n_ids = torch.topk(-A, self.k_sample, dim=1)[1][-1]
		top_n = torch.index_select(h, dim=0, index=top_n_ids)
		p_targets = self.create_positive_targets(self.k_sample, device)
		n_targets = self.create_negative_targets(self.k_sample, device)

		all_targets = torch.cat([p_targets, n_targets], dim=0)
		all_instances = torch.cat([top_p, top_n], dim=0)
		#Or
		all_ids = torch.cat([top_p_ids, top_n_ids]) #RL
		logits = classifier(all_instances)
		all_preds = torch.topk(logits, 1, dim = 1)[1].squeeze(1)
		instance_loss = self.instance_loss_fn(logits, all_targets)
		#Or return instance_loss, all_preds, all_targets
		return instance_loss, all_preds, all_targets, logits, all_ids #RL
	
	#instance-level evaluation for out-of-the-class attention branch
	def inst_eval_out(self, A, h, classifier):
		device=h.device
		if len(A.shape) == 1:
			A = A.view(1, -1)
		top_p_ids = torch.topk(A, self.k_sample)[1][-1]
		top_p = torch.index_select(h, dim=0, index=top_p_ids)
		p_targets = self.create_negative_targets(self.k_sample, device)
		logits = classifier(top_p)
		p_preds = torch.topk(logits, 1, dim = 1)[1].squeeze(1)
		instance_loss = self.instance_loss_fn(logits, p_targets)
		#Or return instance_loss, p_preds, p_targets
		return instance_loss, p_preds, p_targets, logits, top_p_ids #RL

	def forward(self, h, label=None, instance_eval=False, return_features=False, attention_only=False):
		device = h.device
		A, h = self.attention_net(h)  # NxK		
		A = torch.transpose(A, 1, 0)  # KxN
		if attention_only:
			return A
		A_raw = A
		A = F.softmax(A, dim=1)  # softmax over N

		if instance_eval:
			total_inst_loss = 0.0
			all_preds = []
			all_targets = []
			#Or
			all_logits = []
			all_ids = [] #RL
			inst_labels = F.one_hot(label, num_classes=self.n_classes).squeeze() #binarize label
			for i in range(len(self.instance_classifiers)):
				inst_label = inst_labels[i].item()
				classifier = self.instance_classifiers[i]
				if inst_label == 1: #in-the-class:
					#Or instance_loss, preds, targets = self.inst_eval(A, h, classifier)
					instance_loss, preds, targets, instances, ids = self.inst_eval(A, h, classifier) #RL
					all_preds.extend(preds.cpu().numpy())
					all_targets.extend(targets.cpu().numpy())
					#Or
					all_logits.extend(instances.cpu().detach().numpy()) ## can't call numpy on var that requires grad
					all_ids.extend(ids.cpu().numpy()) #RL
				else: #out-of-the-class
					if self.subtyping:
						instance_loss, preds, targets = self.inst_eval_out(A, h, classifier)
						all_preds.extend(preds.cpu().numpy())
						all_targets.extend(targets.cpu().numpy())
						#Or
						all_logits.extend(instances.cpu().detach().numpy())
						all_ids.extend(ids.cpu().numpy()) #RL
					else:
						continue
				total_inst_loss += instance_loss

			if self.subtyping:
				total_inst_loss /= len(self.instance_classifiers)
				
		M = torch.mm(A, h) 
		logits = self.classifiers(M)
		Y_hat = torch.topk(logits, 1, dim = 1)[1]
		Y_prob = F.softmax(logits, dim = 1)
		if instance_eval:
			results_dict = {
				'instance_loss': total_inst_loss,
				'inst_labels': np.array(all_targets), 
				'inst_preds': np.array(all_preds),
				#Or
				'instances': np.array(all_logits),
				'ids': np.array(all_ids) #RL
			}
		else:
			results_dict = {}
		if return_features:
			results_dict.update({'features': M})
		return logits, Y_prob, Y_hat, A_raw, results_dict

class CLAM_MB(CLAM_SB):
	def __init__(self, gate = True, size_arg = "small", dropout = False, k_sample=8, n_classes=2,
		instance_loss_fn=nn.CrossEntropyLoss(), subtyping=False):
		nn.Module.__init__(self)
		#self.size_dict = {"small": [1024, 512, 256], "big": [1024, 512, 384]}
		self.size_dict = {"small": [207, 100, 50], "big": [207, 100, 50]}
		size = self.size_dict[size_arg]
		fc = [nn.Linear(size[0], size[1]), nn.ReLU()]
		if dropout:
			fc.append(nn.Dropout(0.25))
		if gate:
			attention_net = Attn_Net_Gated(L = size[1], D = size[2], dropout = dropout, n_classes = n_classes)
		else:
			attention_net = Attn_Net(L = size[1], D = size[2], dropout = dropout, n_classes = n_classes)
		fc.append(attention_net)
		self.attention_net = nn.Sequential(*fc)
		bag_classifiers = [nn.Linear(size[1], 1) for i in range(n_classes)] #use an indepdent linear layer to predict each class
		self.classifiers = nn.ModuleList(bag_classifiers)
		instance_classifiers = [nn.Linear(size[1], 2) for i in range(n_classes)]
		self.instance_classifiers = nn.ModuleList(instance_classifiers)
		self.k_sample = k_sample
		self.instance_loss_fn = instance_loss_fn
		self.n_classes = n_classes
		self.subtyping = subtyping
		initialize_weights(self)

	def forward(self, h, label=None, instance_eval=False, return_features=False, attention_only=False):
		device = h.device
		A, h = self.attention_net(h)  # NxK		
		A = torch.transpose(A, 1, 0)  # KxN
		if attention_only:
			return A
		A_raw = A
		A = F.softmax(A, dim=1)  # softmax over N

		if instance_eval:
			total_inst_loss = 0.0
			all_preds = []
			all_targets = []
			inst_labels = F.one_hot(label, num_classes=self.n_classes).squeeze() #binarize label
			for i in range(len(self.instance_classifiers)):
				inst_label = inst_labels[i].item()
				classifier = self.instance_classifiers[i]
				if inst_label == 1: #in-the-class:
					instance_loss, preds, targets = self.inst_eval(A[i], h, classifier)
					all_preds.extend(preds.cpu().numpy())
					all_targets.extend(targets.cpu().numpy())
				else: #out-of-the-class
					if self.subtyping:
						instance_loss, preds, targets = self.inst_eval_out(A[i], h, classifier)
						all_preds.extend(preds.cpu().numpy())
						all_targets.extend(targets.cpu().numpy())
					else:
						continue
				total_inst_loss += instance_loss

			if self.subtyping:
				total_inst_loss /= len(self.instance_classifiers)

		M = torch.mm(A, h) 
		logits = torch.empty(1, self.n_classes).float().to(device)
		for c in range(self.n_classes):
			logits[0, c] = self.classifiers[c](M[c])
		Y_hat = torch.topk(logits, 1, dim = 1)[1]
		Y_prob = F.softmax(logits, dim = 1)
		if instance_eval:
			results_dict = {'instance_loss': total_inst_loss, 'inst_labels': np.array(all_targets), 
			'inst_preds': np.array(all_preds)}
		else:
			results_dict = {}
		if return_features:
			results_dict.update({'features': M})
		return logits, Y_prob, Y_hat, A_raw, results_dict


In [23]:
args = pd.DataFrame({'dir_project': '/Users/chitrakbanerjee/Desktop/omics/new_dev/',
        'dir_code': '/Users/chitrakbanerjee/Desktop/omics/new_dev/',
        'results_dir': '/Users/chitrakbanerjee/Desktop/omics/new_dev/result/',
        'dir_oniput': '/Users/chitrakbanerjee/Desktop/omics/new_dev/',
        'dir_split' : '/Users/chitrakbanerjee/Desktop/omics/new_dev/split/',
        'dir_result' : '/Users/chitrakbanerjee/Desktop/omics/new_dev/result/',
        'cv_fold': 5,
        'cv_val': 0.2,
        'cv_test': 0.2,
        'cv_train': 0.6,
        'cv_equal': True,
        'opt': 'adam',
        'log_data': True,
        'n_classes': 2,
        'lr': 1e-4,
        'reg': 1e-5,
        'drop_out': True,
        'weighted_sample': True,
        'max_epochs': 400,
        'early_stopping': False,
        'model_type': 'clam_mb',
        'bag_loss': 'svm',
        'inst_loss': 'ce',
        'bag_weight': 0.7,
        'B': 2,
        'model_size': 'small',
        'no_inst_cluster': False,
        'subtyping': False,
        'log_data': True,
        'testing': False
       }, index = [0])
# # %% Adding Arguments
# dir_project = '/SFS/user/ry/ohjihw/project/015'
# parser.add_argument( '--dir_project', type=str, default=dir_project )
# parser.add_argument( '--dir_code', type=str, default='code/python' )
# parser.add_argument( '--dir_oniput', type=str, default='oniput' )
# parser.add_argument( '--dir_split', type=str, default='split' )
# parser.add_argument( '--dir_result', type=str, default='result' )
# ###
# parser.add_argument( '--job_data', type=str, default='20230412-1-HM' )
# parser.add_argument( '--job_task', type=str, default='Tubules' )
# parser.add_argument( '--job_label', type=str, default='CASE' )
# ###
# parser.add_argument( '--seed', type=int, default=1 )
# ###
# '''
# parser.add_argument( '--cv_fold', type=int, default=100 )
# parser.add_argument( '--cv_val', type=float, default=0.2 )
# parser.add_argument( '--cv_test', type=float, default=0.2 )
# '''
# parser.add_argument( '--cv_fold', type=int, default=1 )
# parser.add_argument( '--cv_val', type=float, default=0.0 )
# parser.add_argument( '--cv_test', type=float, default=0.0 )
# parser.add_argument( '--cv_train', type=float, default=1.0 )
# parser.add_argument( '--cv_equal', type=bool, default=True )
# ###
# parser.add_argument( '--opt', type=str, choices=[ 'adam', 'sgd' ], default='adam' )
# parser.add_argument( '--lr', type=float, default=1e-4, \
# 	help='learning rate (default: 1e-4)' )
# parser.add_argument( '--reg', type=float, default=1e-5, \
# 	help='weight decay (default: 1e-5)' )
# parser.add_argument( '--drop_out', action='store_true', default=True, \
# 	help='enabel dropout (p=0.25)' )
# parser.add_argument( '--weighted_sample', action='store_true', default=True, \
# 	help='enable weighted sampling' )
# parser.add_argument( '--max_epochs', type=int, default=400, \
# 	help='maximum number of epochs to train (default: 200)' )
# parser.add_argument( '--early_stopping', action='store_true', default=False, \
# 	help='enable early stopping' )
# ### CLAM
# parser.add_argument( '--model_type', type=str, choices=[ 'clam_sb', 'clam_mb', 'mil' ], default='clam_sb', \
# 	help='type of model (default: clam_sb, clam w/ single attention branch)' )
# parser.add_argument( '--bag_loss', type=str, choices=[ 'svm', 'ce' ], default='ce', \
# 	help='sample-level classification loss function (default: ce)' )
# parser.add_argument( '--inst_loss', type=str, choices=[ 'svm', 'ce', None ], default='svm', \
# 	help='instance-level clustering loss function (default: None)' )
# parser.add_argument( '--bag_weight', type=float, default=0.7, \
# 	help='clam: weight coefficient for bag-level loss (default: 0.7)' )
# parser.add_argument( '--B', type=int, default=10, \
# 	help='numbr of positive/negative patches to sample for clam' )
# parser.add_argument( '--model_size', type=str, choices=[ 'small', 'big' ], default='small', \
# 	help='size of model, does not affect mil' )
# parser.add_argument( '--no_inst_cluster', action='store_true', default=False, \
# 	help='disable instance-level clustering' )
# parser.add_argument( '--subtyping', action='store_true', default=False, \
# 	help='subtyping problem' )
# 	# In case you want to modify, maybe try first with 'bag_weight' and 'B'. - JO
# ### Miscellaneous
# parser.add_argument( '--log_data', action='store_true', default=True, \
# 	help='log data using tensorboard' )
# parser.add_argument( '--testing', action='store_true', default=False, \
# 	help='debugging tool' )


In [24]:
# %% General Modules
import itertools
import math
import pdb
import random
###
import numpy as np
import pandas as pd

# %% Special Modules - deep learning
import torch
#from torch.utils.data import DataLoader, sampler
#import torch.nn as nn
#import torch.nn.functional as F
###
device = torch.device( "cuda" if torch.cuda.is_available() else "cpu" )

# %% Internal Modules
from datasets.dataset_generic import Generic_MIL_Dataset
from utils.core_utils import train
from utils.file_utils import load_pkl, save_pkl
from utils.utils import *

# %%

# %% [markdown]
## Preprocessing

# %% Data

dataset = Generic_MIL_Dataset(
		data_dir = '/Users/chitrakbanerjee/Desktop/omics/new_dev/',
		csv_path = os.path.join( '/Users/chitrakbanerjee/Desktop/omics/new_dev/', 'bag.csv' ),
		label_dict = { 'CTR': 0, "CASE": 1 },
		seed=1, patient_strat=True, ignore=[]
	)

# %%

# %% [markdown]
## Functions

# %% Seeding
def seed_torch(seed):
	random.seed(seed)
	os.environ['PYTHONHASHSEED'] = str(seed)
	np.random.seed(seed)
	torch.manual_seed(seed)
	if device.type == 'cuda':
		torch.cuda.manual_seed(seed)
		torch.cuda.manual_seed_all(seed) # if you are using multi-GPU.
	torch.backends.cudnn.benchmark = False
	torch.backends.cudnn.deterministic = True

# %% Single Run of CLAM-SMILE
def runSingle( f, args ):
	( train_dataset, val_dataset, test_dataset ) = dataset.return_splits(
		from_id = False, 
		csv_path = os.path.join( '/Users/chitrakbanerjee/Desktop/omics/new_dev/split/', '{}_{}_{}_{}'.format(
			int( 100 * cv_val ), int( 100 * cv_test ), cv_fold, f
		) + '.csv' ),
		val_frac=args['cv_val'].item(), test_frac=args['cv_test'].item()
	)
	datasets = ( train_dataset, val_dataset, test_dataset )
	return train( datasets, f, args )

# %%

# %% [markdown]
## Main

# %% Main
if __name__ == "__main__":
    args.results_dir = '{}/{}_{}_{}'.format( args['dir_result'].item(),
        int( 100 * args['cv_val'].item() ), int( 100 * args['cv_test'].item() ),
                                            args['cv_fold'].item())
    os.makedirs( args['results_dir'].item(), exist_ok=True )
    ###
    folds = np.arange( 0, args['cv_fold'].item())

    all_stopping_epoch = []
    all_train_auc = []
    all_train_acc = []
    all_val_auc = []
    all_val_acc = []
    all_test_auc = []
    all_test_acc = []
    ###
    all_train_acc_vec = []
    all_train_auc_vec = []
    all_val_acc_vec = []
    all_val_auc_vec = []
    ###
    for f in folds:
        (results, train_auc, train_acc, val_auc, val_acc, test_auc, test_acc,
         stopping_epoch, train_acc_vec, train_auc_vec,
         val_acc_vec, val_auc_vec) = runSingle( f, args )
        all_stopping_epoch.append(stopping_epoch)
        all_train_auc.append(train_auc)
        all_train_acc.append(train_acc)
        if cv_val > 0:
            all_val_auc.append(val_auc)
            all_val_acc.append(val_acc)
        else:
            all_val_auc.append(-1)
            all_val_acc.append(-1)
        if cv_test > 0:
            all_test_auc.append(test_auc)
            all_test_acc.append(test_acc)
        else:
            all_test_auc.append(-1)
            all_test_acc.append(-1)
        all_train_acc_vec.append( train_acc_vec )
        all_train_auc_vec.append( train_auc_vec )
        all_val_acc_vec.append( val_acc_vec )
        all_val_auc_vec.append( val_auc_vec )
        ###
        results_dir = args['results_dir'].item()
        path = '{}/{}.pkl'.format( results_dir, f )
        save_pkl( path, results )
        ###
        conv = pd.DataFrame( {'train_acc': train_acc_vec, 'train_auc': train_auc_vec,
            'val_acc': val_acc_vec, 'val_auc': val_auc_vec} )
        path = '{}/{}.csv'.format( results_dir, f )
        conv.to_csv(path)
    ###
    final_df = pd.DataFrame({'folds': folds, 'stopping_epoch': all_stopping_epoch,
        'train_auc': all_train_auc, 'train_acc' : all_train_acc, 'val_auc': all_val_auc,
        'val_acc' : all_val_acc, 'test_auc': all_test_auc, 'test_acc' : all_test_acc} )
    ###
    final_df = final_df.append( { 'folds': '', 'stopping_epoch': np.mean(all_stopping_epoch),
        'train_auc': np.mean(all_train_auc),
        'train_acc' : np.mean(all_train_acc),
        'val_auc': np.mean(all_val_auc),
        'val_acc': np.mean(all_val_acc),
        'test_auc': np.mean(all_test_auc),
        'test_acc': np.mean(all_test_acc)
    }, ignore_index = True )
    ###
    print(final_df)
    path = '{}/summary.csv'.format( results_dir )
    final_df.to_csv(path)
    ###
    print("finished!")
print("end script")

# %%

# %% [markdown]
## EoF


label column: label
label dictionary: {'CTR': 0, 'CASE': 1}
number of classes: 2
slide-level counts:  
 0    37
1    16
Name: label, dtype: int64
Patient-LVL; Number of samples registered in class 0: 37
Slide-LVL; Number of samples registered in class 0: 37
Patient-LVL; Number of samples registered in class 1: 16
Slide-LVL; Number of samples registered in class 1: 16

Training Fold 0!

Init train/val/test splits... 
Done!
Training on 41 samples
Validating on 6 samples
Testing on 6 samples

Init loss function... Setting tau to 1.0
Done!

Init Model... Done!
CLAM_MB(
  (attention_net): Sequential(
    (0): Linear(in_features=315, out_features=100, bias=True)
    (1): ReLU()
    (2): Dropout(p=0.25, inplace=False)
    (3): Attn_Net_Gated(
      (attention_a): Sequential(
        (0): Linear(in_features=100, out_features=50, bias=True)
        (1): Tanh()
        (2): Dropout(p=0.25, inplace=False)
      )
      (attention_b): Sequential(
        (0): Linear(in_features=100, out_features=5

the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
batch 19, loss: 0.0000, instance_loss: 4708.4155, weighted_loss: 1412.5247, label: 1, bag_size: 18
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample valu

epoch:9


the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
batch 19, loss: 4582.4302, instance_loss: 5147.8760, weighted_loss: 4752.0640, label: 1, bag_size: 34
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the 

the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
batch 39, loss: 27945.4922, instance_loss: 11206.6982, weighted_loss: 22923.8535, label: 0, bag_size: 15
the k_sample value is:  2


class 0 clustering acc 0.5609756097560976: correct 46/82
class 1 clustering acc 0.524390243902439: correct 43/82
Epoch: 13, train_loss: 8749.1497, train_clustering_loss:  13441.1966, train_error: 0.5854
class 0: acc 0.43478260869565216, correct 10/23
class 1: acc 0.3888888888888889, correct 7/18
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  

epoch:18


the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
batch 19, loss: 10274.6797, instance_loss: 13885.4492, weighted_loss: 11357.9102, label: 1, bag_size: 19
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2


...

the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
batch 39, loss: 0.0000, instance_loss: 0.0000, weighted_loss: 0.0000, label: 0, bag_size: 25
the k_sample value is:  2


class 0 clustering acc 0.5487804878048781: correct 45/82
class 1 clustering acc 0.6951219512195121: correct 57/82
Epoch: 384, train_loss: 893.8063, train_clustering_loss:  2255.3042, train_error: 0.3415
class 0: acc 0.7142857142857143, correct 15/21
class 1: acc 0.6, correct 12/20
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2

Val Set, val_loss: 1651.9757, val_error: 0.1667, auc: 0.8333
class 0 clustering acc 0.6666666666666666: correct 8/12
class 1 clustering acc 0.6666666666666666: correct 8/12
class 0: acc 1.0, correct 3/3
class 1: acc 0.6666666666666666, correct 2/3
epoch:385


the k_sample value is:  

epoch:389


the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
batch 19, loss: 9618.2617, instance_loss: 1268.5547, weighted_loss: 7113.3496, label: 0, bag_size: 14
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
th

the k_sample value is:  2
the k_sample value is:  2
batch 39, loss: 0.0000, instance_loss: 5795.1592, weighted_loss: 1738.5479, label: 1, bag_size: 19
the k_sample value is:  2


class 0 clustering acc 0.6829268292682927: correct 56/82
class 1 clustering acc 0.7073170731707317: correct 58/82
Epoch: 393, train_loss: 1456.0117, train_clustering_loss:  2299.2084, train_error: 0.2439
class 0: acc 0.7368421052631579, correct 14/19
class 1: acc 0.7727272727272727, correct 17/22
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2

Val Set, val_loss: 2189.4258, val_error: 0.1667, auc: 0.8333
class 0 clustering acc 0.5: correct 6/12
class 1 clustering acc 0.5833333333333334: correct 7/12
class 0: acc 1.0, correct 3/3
class 1: acc 0.6666666666666666, correct 2/3
epoch:394


the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample valu

the k_sample value is:  2
the k_sample value is:  2
batch 19, loss: 0.0000, instance_loss: 1748.5793, weighted_loss: 524.5739, label: 0, bag_size: 21
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
the k_sample value is:  2
batch 39, loss: 0.0000, instance_loss: 2293.8699, weighted_loss: 688.1610, label: 0, bag_size: 22
the k_sample value is:  2


class 0 clustering acc 0.6097560975609756: correct 50/82
class 1 clustering acc 0.7439024390243902: correct 61/82
Epoch: 398, train_loss: 791.7884, train_clustering_loss:  2079.3654, train_error: 0.2439
c

/var/folders/45/fswzhp4j1qx7m6_9ty17lp500000gn/T/ipykernel_11858/3906308797.py:131: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_df = final_df.append( { 'folds': '', 'stopping_epoch': np.mean(all_stopping_epoch),


In [ ]:
# %% [markdown]
## Command Line Interfaces

# %% Creating a Parser
# import argparse
# parser = argparse.ArgumentParser()

# # %% Adding Arguments
# dir_project = '/SFS/user/ry/ohjihw/project/015'
# parser.add_argument( '--dir_project', type=str, default=dir_project )
# parser.add_argument( '--dir_code', type=str, default='code/python' )
# parser.add_argument( '--dir_oniput', type=str, default='oniput' )
# parser.add_argument( '--dir_split', type=str, default='split' )
# parser.add_argument( '--dir_result', type=str, default='result' )
# ###
# parser.add_argument( '--job_data', type=str, default='20230412-1-HM' )
# parser.add_argument( '--job_task', type=str, default='Glomeruli' )
# parser.add_argument( '--job_task', type=str, default='Tubules' )
# parser.add_argument( '--job_label', type=str, default='CASE' )
# ###
# parser.add_argument( '--cv_fold', type=int, default=1 )
# parser.add_argument( '--cv_val', type=float, default=0.0 )
# parser.add_argument( '--cv_test', type=float, default=0.0 )
# parser.add_argument( '--cv_train', type=float, default=1.0 )
# parser.add_argument( '--cv_equal', type=bool, default=True )
# ###
# parser.add_argument( '--opt', type=str, choices=[ 'adam', 'sgd' ], default='adam' )
# parser.add_argument( '--lr', type=float, default=1e-4, \
# 	help='learning rate (default: 1e-4)' )
# parser.add_argument( '--reg', type=float, default=1e-5, \
# 	help='weight decay (default: 1e-5)' )
# parser.add_argument( '--drop_out', action='store_true', default=True, \
# 	help='enabel dropout (p=0.25)' )
# parser.add_argument( '--weighted_sample', action='store_true', default=True, \
# 	help='enable weighted sampling' )
# parser.add_argument( '--max_epochs', type=int, default=400, \
# 	help='maximum number of epochs to train (default: 200)' )
# parser.add_argument( '--early_stopping', action='store_true', default=False, \
# 	help='enable early stopping' )
# ### CLAM
# parser.add_argument( '--model_type', type=str, choices=[ 'clam_sb', 'clam_mb', 'mil' ], default='clam_sb', \
# 	help='type of model (default: clam_sb, clam w/ single attention branch)' )
# parser.add_argument( '--bag_loss', type=str, choices=[ 'svm', 'ce' ], default='ce', \
# 	help='sample-level classification loss function (default: ce)' )
# parser.add_argument( '--inst_loss', type=str, choices=[ 'svm', 'ce', None ], default='svm', \
# 	help='instance-level clustering loss function (default: None)' )
# parser.add_argument( '--bag_weight', type=float, default=0.7, \
# 	help='clam: weight coefficient for bag-level loss (default: 0.7)' )
# parser.add_argument( '--B', type=int, default=10, \
# 	help='numbr of positive/negative patches to sample for clam' )
# parser.add_argument( '--model_size', type=str, choices=[ 'small', 'big' ], default='small', \
# 	help='size of model, does not affect mil' )
# parser.add_argument( '--no_inst_cluster', action='store_true', default=False, \
# 	help='disable instance-level clustering' )
# parser.add_argument( '--subtyping', action='store_true', default=False, \
# 	help='subtyping problem' )
# 	# In case you want to modify, maybe try first with 'bag_weight' and 'B'. - JO
# ### Miscellaneous
# parser.add_argument( '--log_data', action='store_true', default=True, \
# 	help='log data using tensorboard' )
# parser.add_argument( '--testing', action='store_true', default=False, \
# 	help='debugging tool' )

# %% Parsing Arguments
in_ipython = hasattr(__builtins__,'__IPYTHON__')
args = parser.parse_args("") if in_ipython else parser.parse_args()
for ( key, value ) in vars(args).items():
	print( 'args' + '.' + key + ':', value )

# %%

# %% [markdown]
## Header

# %% Working Directory
import os
args.dir_code = os.path.join( args.dir_project, args.dir_code )
print( 'args.dir_code:', args.dir_code )
os.chdir( args.dir_code )
args.dir_oniput = os.path.join( args.dir_project, args.dir_oniput )
args.dir_oniput = os.path.join( args.dir_oniput, args.job_data )
args.dir_oniput = os.path.join( args.dir_oniput, args.job_task )
print( 'args.dir_ioput:', args.dir_oniput )
args.dir_split = os.path.join( args.dir_oniput, args.dir_split )
os.makedirs( args.dir_split, exist_ok=True )
args.dir_result = os.path.join( args.dir_oniput, args.dir_result )
os.makedirs( args.dir_result, exist_ok=True )

# %% General Modules
import itertools
import math
import pdb
import random
###
import matplotlib.pylab as plt
import numpy as np
import pandas as pd
import seaborn as sns

# %% Special Modules - deep learning
import torch
import torch.nn.functional as F
###
device = torch.device( "cuda" if torch.cuda.is_available() else "cpu" )

# %% Internal Modules
from models.model_clam import CLAM_MB, CLAM_SB
from utils.utils import *
from utils.file_utils import save_pkl, load_pkl

# %%

# %% [markdown]
## Preparation

# %%
def initiate_model(model_args, ckpt_path):
    print('Init Model')    
    model_dict = {
		"dropout": model_args.drop_out,
		'n_classes': 2, # model_args.n_classes,
		"k_sample": model_args.k_sample
	}
    if model_args.model_size is not None and model_args.model_type in ['clam_sb', 'clam_mb']:
        model_dict.update({"size_arg": model_args.model_size})
    if model_args.model_type =='clam_sb':
        model = CLAM_SB(**model_dict)
    elif model_args.model_type =='clam_mb':
        model = CLAM_MB(**model_dict)
    else: # args.model_type == 'mil'
        if model_args.n_classes > 2:
            model = MIL_fc_mc(**model_dict)
        else:
            model = MIL_fc(**model_dict)
    print_network(model)
    ckpt = torch.load(ckpt_path)
    #print_network(ckpt)
    ckpt_clean = {}
    for key in ckpt.keys():
        if 'instance_loss_fn' in key:
            continue
        ckpt_clean.update({key.replace('.module', ''):ckpt[key]})
    model.load_state_dict(ckpt_clean, strict=True)
    model.relocate()
    model.eval()
    return model

# %%
def infer_single_slide(model, features, label, reverse_label_dict, k=1, instance_eval = False, label_tensor = None):
	features = features.to(device)
	with torch.no_grad():
		if isinstance(model, (CLAM_SB,)):
			#model_results_dict = model(features)
			logits, Y_prob, Y_hat, A, results_dict = model(features, instance_eval = instance_eval, label = label_tensor)
			print(results_dict)
			Y_hat = Y_hat.item()
			if isinstance(model, (CLAM_MB,)):
				A = A[Y_hat]
			A = A.view(-1, 1).cpu().numpy()
		else:
			raise NotImplementedError
		print('Y_hat: {}, Y: {}, Y_prob: {}'.format(reverse_label_dict[Y_hat], label, ["{:.4f}".format(p) for p in Y_prob.cpu().flatten()]))
		probs, ids = torch.topk(Y_prob, k)
		probs = probs[-1].cpu().numpy()
		ids = ids[-1].cpu().numpy()
		preds_str = np.array([reverse_label_dict[idx] for idx in ids])
	return ids, preds_str, probs, A, results_dict


# %%

# %% [markdown]
## Line by Line

# %%
def extract_attention_scores(args, cell_barcode_path, ckpt_path, feature_path, meta_path):
	###
	cell_barcode_dict = load_pkl(cell_barcode_path)
	metadata = pd.read_csv(meta_path)
	files = os.listdir(feature_path)
	cell_weights = torch.Tensor()
	###
	sample_list = []
	barcode_list = []
	results_dict_list = []
	###
	for f in files:
		features = torch.load(os.path.join(feature_path, f))
		model = initiate_model(args, ckpt_path)
		sample_id = f.split('.')[0]
		if sample_id not in str( cell_barcode_dict.keys() ):
			continue
		cell_barcodes = cell_barcode_dict[ int( sample_id )]
		label = metadata[ metadata['slide_id'] == int( sample_id )].label.values[0]
		label_dict = {'CTR':0, 'CASE':1 }
		class_labels = list(label_dict.keys())
		class_encodings = list(label_dict.values())
		label_tensor = torch.tensor([label_dict[label]])
		reverse_label_dict = {class_encodings[i]: class_labels[i] for i in range(len(class_labels))} 
		ids, preds_str, probs, A, results_dict  = infer_single_slide(model, features, label, reverse_label_dict, k=1,
														instance_eval = True, label_tensor= label_tensor)
		weights = F.softmax(torch.Tensor(A), dim = 0).view(1, -1)
		cell_weights = torch.cat((cell_weights, weights), dim = 1)
		sample_list.extend(np.repeat(sample_id, features.shape[0]))
		barcode_list.extend(cell_barcodes)
		results_dict_list.append(results_dict)
	return cell_weights, sample_list, barcode_list, results_dict_list

# %% [markdown]
## Main

# %%
args.results_dir = '{}/{}_{}_{}'.format(
	args.dir_result,
	int( 100 * args.cv_val ), int( 100 * args.cv_test ), args.cv_fold
)
###
cell_barcode_path = "{}/insts_in_bags.pkl".format( args.dir_oniput )
ckpt_path = "{}/s_0_checkpoint.pt".format( args.results_dir )
feature_path = "{}/bags".format( args.dir_oniput )
meta_path = "{}/bag.csv".format( args.dir_oniput )

#%%
args.ckpt_path = ckpt_path # os.path.join(ckpt_path, f, 's_0_checkpoint.pt')
args.k_sample = args.B #int(f.split('_B_')[1].split('_bag')[0])
(
	cell_weights,
	sample_list,
	barcode_list,
	results_dict_list
) = extract_attention_scores(
	args,
	cell_barcode_path, #args.barcode_path,
	ckpt_path, #args.ckpt_path,
	feature_path, #args.feature_path, 
	meta_path #args.meta_path
)

# %%
DF = pd.DataFrame( {
	'bag': sample_list,
	'inst': barcode_list,
	'weight': cell_weights[0,:]
} )
DF

# %%
path = "{}/weights.csv".format( args.results_dir )
DF.to_csv(path)

# %%

# %% [markdown]
## EoF


In [1]:
from topk.svm import SmoothTop1SVM

In [31]:
output = torch.randn(10, 1)

In [32]:
output

tensor([[ 0.5221],
        [ 0.0993],
        [ 1.2200],
        [ 0.2630],
        [ 0.0533],
        [-0.0296],
        [ 0.1782],
        [-0.8404],
        [-0.7691],
        [ 1.0615]])

In [33]:
output.view(1, -1)

tensor([[ 0.5221,  0.0993,  1.2200,  0.2630,  0.0533, -0.0296,  0.1782, -0.8404,
         -0.7691,  1.0615]])

In [34]:
maxk = 1
torch.topk(output, 1)

torch.return_types.topk(
values=tensor([[ 0.5221],
        [ 0.0993],
        [ 1.2200],
        [ 0.2630],
        [ 0.0533],
        [-0.0296],
        [ 0.1782],
        [-0.8404],
        [-0.7691],
        [ 1.0615]]),
indices=tensor([[0],
        [0],
        [0],
        [0],
        [0],
        [0],
        [0],
        [0],
        [0],
        [0]]))

In [35]:
len(output.view(1, -1).shape)

2

In [23]:
maxk = 2
torch.topk(output, 1)[1][-1]

tensor([1])

In [16]:
args['cv_val'].item()

0.2

In [10]:
csv_path = os.path.join( '/Users/chitrakbanerjee/Desktop/omics/new_dev/split/', '{}_{}_{}_{}'.format(int( 100 * cv_val ), 
        int( 100 * cv_test ), cv_fold, f) + '.csv' )

In [11]:
d = dataset.return_splits(from_id=False, csv_path=csv_path, val_frac=0.2, test_frac=0.2 )

In [12]:
train_split = dataset.get_split_from_df(pd.read_csv(csv_path), 'train')

In [13]:
train_split[0]

(tensor([[7.6374e-01, 2.9191e-01, 4.6722e-02,  ..., 2.5534e+02, 2.6834e+02,
          2.8834e+02],
         [7.6065e-01, 3.1171e-01, 4.9396e-02,  ..., 4.6671e+02, 4.8443e+02,
          5.0843e+02],
         [7.1368e-01, 3.7529e-01, 6.6800e-02,  ..., 1.7643e+02, 1.8714e+02,
          2.0361e+02],
         ...,
         [7.5604e-01, 2.9954e-01, 4.7077e-02,  ..., 9.6748e+01, 1.0521e+02,
          1.1272e+02],
         [7.6887e-01, 3.0632e-01, 2.8374e-02,  ..., 1.6174e+02, 1.6955e+02,
          1.7655e+02],
         [7.6065e-01, 3.3915e-01, 2.0174e-02,  ..., 1.5948e+02, 1.6918e+02,
          1.7818e+02]]),
 0)

In [36]:
test_dataset[0][0]

tensor([[7.5540e-01, 2.9897e-01, 5.7978e-02,  ..., 4.0787e+02, 4.2369e+02,
         4.4192e+02],
        [7.3131e-01, 3.3108e-01, 7.8102e-02,  ..., 4.1476e+02, 4.3185e+02,
         4.5124e+02],
        [7.4528e-01, 3.3066e-01, 5.4547e-02,  ..., 4.1105e+02, 4.2760e+02,
         4.4498e+02],
        ...,
        [7.6000e-01, 3.0634e-01, 5.9379e-02,  ..., 3.5635e+02, 3.6736e+02,
         3.8192e+02],
        [7.7293e-01, 2.9386e-01, 3.7334e-02,  ..., 3.5137e+02, 3.6224e+02,
         3.7637e+02],
        [7.5152e-01, 3.4991e-01, 1.1812e-02,  ..., 1.3392e+02, 1.5302e+02,
         2.0238e+02]])